In [1]:
#clean_extrator_access_PA
#clean_ImputacaoDeDados_PA
#clean_Trata_dados
#clean_Padroes_PA_estatisticas_com_Whitecoat_Dir_PA
#clean_kmeans_random_forest9approaches_completo

In [2]:
%matplotlib inline
%config InlineBackend.figure_formats = ['png']
# %config InlineBackend.figure_formats = ['svg']

In [3]:
import itertools
import math
import numpy as np
import pandas as pd
import pyodbc
import typing as T
from datetime import  date, datetime, time, timedelta
from matplotlib import pyplot as plt
from pathlib import Path


In [4]:
# Configurações regionais para formatação de números, etc (ex. separador de milhar'.' e decimal ',')
import locale
locale.setlocale(locale.LC_ALL, 'pt_BR.utf-8')

# Definição se disco C: (laptop) ou D: (desktop) 
config_dirs = open("prefixo_dados.txt").readlines() 
DIR_PREFIXO = Path(config_dirs[0].strip())

DIR_DATASET = DIR_PREFIXO / "PA_clean" / "dataset"
DIR_DESFECHO = DIR_PREFIXO / "PA_clean" / "desfecho"

In [5]:
# IDADE >=60 then é idoso, else é jovem
# PERÍODOS 
#      Matutino 6h-8h59
#      Diurno 9h-20h59
#      Vespertino 21h-00h59
#      Noturno 1h-05h59

# slice para gerar os horários de cada turno

matutino = (time(6,0), time(9,0))
diurno = (time(9,0), time(21,0))
vespertino = (time(21,0), time(23,0))
noturno = (time(23,0), time(6,0))

In [6]:
# list(mapas.columns)    

In [7]:
#  Processo de importação dos dados a partir de uma base SQL
#  

bases_de_dados = {
    "dados_originais": r"C:\Users\marta\OneDrive\Desktop\DynaMAPA.mdb",
#    "dados_mapas_2021": r"C:\Users\marta\projeto_PA\mapa2021\DynaMAPA.mdb",
#    "cardiomapa": r"D:\Biocardios Dataset\mapa2021\CARDIOMAPA.md1"   
}

#access_path = Path(r"C:\Users\marta\OneDrive\Desktop\DynaMAPA.mdb")
#access_path = Path(r"C:\Users\marta\projeto_PA\mapa2021\DynaMAPA.mdb")
#access_path = Path(r"D:\Biocardios Dataset\mapa2021\CARDIOMAPA.md1")

In [8]:
#  Essas linhas se conectam ao MSAccess como um banco de dados, e puxam
#  os dados brutos a partir de 3 tabelas relacionadas.
#  
#  
#  Os dados são desnormalizados (a informação de nome, gênero, etc.. é replicada em todas as linhas), de 
#  forma que tenhamos todos os dados em um único dataframe inicial para análise.

# Python envia o comando SQL para o BD Access e recebe todos os resultados (fetchall)
def executa_sql(conexao, comando_sql):
    return conexao.execute(comando_sql).fetchall()
    

comando_sql = """SELECT Patients.PatientID, Patients.PatientName, Patients.LastName, Patients.Birthday, Patients.Sex, 
                  Patients.Weight, Patients.Height, Items.DateItem,
                  Items.Systolic, Items.Diastolic, Exams.ExamDate
FROM ExamsItems as Items, Exams as Exams, Patients as Patients 
WHERE Items.ExamID=Exams.ExamID AND  Exams.PatientID=Patients.PatientID  and Patients.PatientID<>1
"""

def le_base_de_dados(access_path):
    conexao = pyodbc.connect(f'Driver={{Microsoft Access Driver (*.mdb, *.accdb)}};DBQ={Path(access_path)};')
    
    dados_extraidos = []
    dados = executa_sql(conexao, comando_sql)
    for linha in dados:
        lista_linha = []
        for item in range(len(linha)):
            if item == 2:
                lista_linha[1] = lista_linha[1] + linha[item]
            else:
                lista_linha.append(linha[item])
        dados_extraidos.append(lista_linha)
        
#        for item in (linha):
#            lista_linha.append(item)
#        dados_extraidos.append(lista_linha)
    
    cabecalho = ['numero_identificacao',
                 'nome',
                 'data_nascimento',
                 'genero',
                 'peso',
                 'altura',
                 'dateitem',
                 'sistolica',
                 'diastolica',
                 'data_exame']
    
    mapas_dos_campos = pd.DataFrame(dados_extraidos, columns=cabecalho )

    mapas_dos_campos.sistolica.loc[mapas_dos_campos.sistolica == 0] = float("NaN")
    mapas_dos_campos.diastolica.loc[mapas_dos_campos.diastolica == 0] = float("NaN")
    return mapas_dos_campos

def le_todas_as_bases():
    dados = []
    for base in bases_de_dados.values():
        dados.append(le_base_de_dados(base))
    mapas_dos_campos = pd.concat(dados, axis=0, ignore_index=True)
    return mapas_dos_campos

mapas_dos_campos = le_todas_as_bases()
mapas_dos_campos

<ipython-input-8-0ceab5995cac>:51: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mapas_dos_campos.sistolica.loc[mapas_dos_campos.sistolica == 0] = float("NaN")
<ipython-input-8-0ceab5995cac>:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mapas_dos_campos.diastolica.loc[mapas_dos_campos.diastolica == 0] = float("NaN")


numero_identificacao                                   nome  \
0                           4            DONIZZETTE PEREIRA DA SILVA   
1                           4            DONIZZETTE PEREIRA DA SILVA   
2                           4            DONIZZETTE PEREIRA DA SILVA   
3                           4            DONIZZETTE PEREIRA DA SILVA   
4                           4            DONIZZETTE PEREIRA DA SILVA   
...                       ...                                    ...   
1655823                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655824                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655825                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655826                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655827                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   

        data_nascimento genero peso altura            dateitem  sistolica  \
0            1923-10-05      M   85    160 2018-09-10 12:39:00      140.0   
1            1923-10-05      M   85    160 2018-09-10 12:48:00        NaN   
2            1923-10-05      M   85    160 2018-09-10 13:03:00        NaN   
3            1923-10-05      M   85    160 2018-09-10 13:18:00        NaN   
4            1923-10-05      M   85    160 2018-09-10 13:33:00        NaN   
...                 ...    ...  ...    ...                 ...        ...   
1655823      1971-01-14      M   99    179 2020-09-11 14:30:00      131.0   
1655824      1971-01-14      M   99    179 2020-09-11 14:45:00      143.0   
1655825      1971-01-14      M   99    179 2020-09-11 15:00:00      138.0   
1655826      1971-01-14      M   99    179 2020-09-11 15:15:00      127.0   
1655827      1971-01-14      M   99    179 2020-09-11 15:28:00        NaN   

         diastolica          data_exame  
0              80.0 2018-09-10 12:25:23  
1               NaN 2018-09-10 12:25:23  
2               NaN 2018-09-10 12:25:23  
3               NaN 2018-09-10 12:25:23  
4               NaN 2018-09-10 12:25:23  
...             ...                 ...  
1655823        91.0 2020-09-10 17:42:01  
1655824        84.0 2020-09-10 17:42:01  
1655825        99.0 2020-09-10 17:42:01  
1655826        89.0 2020-09-10 17:42:01  
1655827         NaN 2020-09-10 17:42:01  

[1655828 rows x 10 columns]

In [9]:
# Agrupa dados de cada paciente (que estão dispersos em uma linha por medida)

mapas_por_paciente = mapas_dos_campos.groupby("numero_identificacao")

def cria_mapas(df):
    """Monta as informações de cada paciente como uma linha do dataframe, na ordem que será usada daqui pra frente"""
    results = []
    for i, paciente in df:
        linha = [paciente.numero_identificacao.iloc[0], paciente.nome.iloc[0],
                 paciente.data_nascimento.iloc[0], paciente.genero.iloc[0],
                 paciente.peso.iloc[0], paciente.altura.iloc[0],
                 paciente.data_exame.iloc[0],
                ]
        
        # Cálculo da idade
        idade = (linha[-1] - linha[2]).days // 365.25

        # Se faltou uma das datas e não foi possível calcular a idade, marca a mesma como NaN - senão 
        # transforma em inteiro:
        if math.isnan(idade):
            print(linha, idade)
            idade = float("NaN")
        else:
            idade = int(idade)
        
        linha.append(idade)
        results.append(linha)
    results = pd.DataFrame(results, columns="numero_identificacao nome data_nascimento genero peso altura data_exame idade".split())
    return results

mapas_agrupado = cria_mapas(mapas_por_paciente)
mapas_agrupado

[1128, 'TESTETESTE', NaT, '', '', '', Timestamp('2019-02-06 09:31:58')] nan
[3957, 'LUIZ GOMES DA COSTA', NaT, '', '80', '170', Timestamp('2019-04-01 16:28:27')] nan
[6602, 'RITA TEIXEIRA DOS REIS NORONHA', NaT, '', '', '', Timestamp('2019-06-04 11:19:21')] nan
[6687, 'MARIA DO CARMO DA CONCEICAO MIRANDA', NaT, '', '', '', Timestamp('2019-06-06 08:01:47')] nan
[7869, 'JOSE ANTONIO RIOS DA SILVA ', NaT, '', '', '', Timestamp('2019-07-05 08:38:10')] nan
[11210, 'JOAO RIBEIRO SIRQUEIRA JUNIOR', NaT, '', '', '', Timestamp('2019-09-26 09:54:19')] nan
[11850, 'REGINA AUXILIADORA PEREIRA TOLEDO', NaT, '', '', '', Timestamp('2019-10-15 08:01:02')] nan
[12212, 'DANIEL LOPES DA CUNHA TORRES DOSSANTOS', NaT, '', '', '', Timestamp('2019-10-22 11:41:43')] nan
[13397, 'TESTE TESTE', NaT, '', '', '', Timestamp('2019-11-23 09:21:23')] nan
[13398, 'TESTE 2CTESTE', NaT, '', '', '', Timestamp('2019-11-23 09:25:20')] nan
[14941, 'REGINA CARVALHO DE OLIVEIRA', NaT, 'F', '80', '167', Timestamp('2020-01-16 1

numero_identificacao                                   nome  \
0                         4            DONIZZETTE PEREIRA DA SILVA   
1                         5                JEFFERSON LUCENA DANTAS   
2                         6                    IGOR DAMASCENO MOTA   
3                         7              ANDREIA DE OLIVEIRA AVILA   
4                         8      CRISTIANO NASCIMENTO POMBO DA PAZ   
...                     ...                                    ...   
21132                 21787              CASTRUZ CATRAMBY COUTINHO   
21133                 21788                 TATIANE ROCHA DA SILVA   
21134                 21791                   MARCOS PAULO PEREIRA   
21135                 21792                      EULINA SOUZA DIAS   
21136                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   

      data_nascimento genero peso altura          data_exame  idade  
0          1923-10-05      M   85    160 2018-09-10 12:25:23   94.0  
1          1948-10-07      M   80    165 2018-12-26 07:39:41   70.0  
2          1999-03-23      M  100    197 2018-12-26 08:06:19   19.0  
3          1978-01-26      F   65   1,64 2018-12-26 08:19:06   40.0  
4          1990-03-07      M  120    172 2018-12-26 08:26:59   28.0  
...               ...    ...  ...    ...                 ...    ...  
21132      1970-10-19      M   90    183 2020-09-10 16:21:02   49.0  
21133      1985-03-15      F   93    167 2020-09-10 16:44:53   35.0  
21134      1973-10-31      M   81    170 2020-09-10 17:26:00   46.0  
21135      1952-04-21      F   64    160 2020-09-10 17:25:50   68.0  
21136      1971-01-14      M   99    179 2020-09-10 17:42:01   49.0  

[21137 rows x 8 columns]

In [10]:
# Celula apenas para visualização dos dados intermediários
##################################################################################################
#pessoa = mapas_por_paciente.get_group(15626)
#pessoa.dateitem[0].date()
#pessoa
# pessoa[pessoa.dateitem > datetime(2018,9, 10, 18,0)].loc[:, "systolic"]



In [11]:
# Exemplo de operação com objetos do tipo "date" e "datetime"

a = datetime(2021, 9,30, 15, 0)
b = date(2020, 10, 1)
(a.date() - b).days

364

In [12]:
#    Normaliza o horário de medidas para contagem a partir de um horario do primeiro dia
#    (ex. a partir das 9h00).
#    
#    ts_col (string): nome da coluna com os dados de timestamp
#    starting_time (datetime.time): [9h00] horario a usar de base para normalizar as medidas 
#    name (str): Name of the resulting series
#    
#    Se o total do periodo de medidas ultrapassar o horário de meia-noite, após 24 horas as medidas
#    darão "overlap" sendo novamente categorizadas no dia 1.
#    
#    O retorno é um pd.Series com os tempos recalculados, ou a partir da 
#    dada-base de 2010-01-01.
#
#    usar o resultado com pd.concat para anexar a coluna de horario ao dataframe original.
 
def normalize_date(df, ts_col, starting_time=time(9,0), name="normalized_ts")->pd.Series:
    
    base = datetime(2010, 1,1, starting_time.hour, starting_time.minute)
    convert = lambda ts: datetime(base.year, base.month, base.day, ts.hour, ts.minute, ts.second)
    date_change_offset = lambda ts: timedelta(seconds=3600 * 24 * int(ts.time() < starting_time)) 
    result =  df.loc[:, ts_col].apply(lambda ts: (base + (convert(ts) - base) + date_change_offset(ts))) 
    result.name = name
    return result

    
#list(normalize_date(pessoa, "dateitem"))
#pessoa

In [13]:
def horario_noturno(hora):
    return (hora >= noturno[0].hour or hora < noturno[1].hour)
   
    
def extract_whitecoat(paciente):

#    Devolve uma sequencia com 4 tuplas de comprimento 3 (horário, medida sistólica, medida diastólica),
#    correspondentes as 4 primeiras medidas tomadas em cada exame.
#    
#    esses 12 valores são guardados em uma coluna a parte no dataframe de saída,
#    e são usados para detectar o padrão 'whitecoat' num momento posterior
    

    try:
        primeira_medida = paciente.dateitem.values[0]
        quarta_medida = paciente.dateitem.values[3]
    except IndexError: 
        # Paciente não tem as 4 primeiras medidas - deixamos as medidas de whitecoat em branco
        print("paciente sem dados das primeiras medidas:", paciente)
        return f"[{','.join('(nan, nan, nan)' for _ in range(4))} ]"
        
    primeiras_medidas = (paciente[paciente.dateitem >= primeira_medida][paciente.dateitem <= quarta_medida]
              [["dateitem", "sistolica", "diastolica"]])
    whitecoat = [tuple(x) for x in primeiras_medidas.to_numpy()]
    whitecoat = str([(ts.strftime("%H:%M") , sist, diast)  for ts, sist, diast in whitecoat])
    return whitecoat
    
    
def transpoe_medidas(dados, limit=None):

#    Transforma as medições na vertical em uma única linha de dados,
#    com as medições em um período de 24h para cada paciente.
#    
#    Recebe um dataframe já com  um "group_by" por paciente, gerado pela 
#    função "mapas_dos_campos" acima.
#    
#    Cria colunas por horario, com intervalos de 15 minutos nos períodos matutino (> 6h00am), diurno e vespertino,
#    e intervalos de 30 min no período noturno (23h00 <= horário < 6h00)
#
#    Para achar a medida correspondente a cada horário, ele procura nos dados a medida
#    no horário mais alto dentro de um intervalo iniciando no horário da coluna:
#    isso é, para a coluna das 17h00, em que o intervalo entre medidas é
#    de 15 minutos, são olhadas as medidas das 17h00 até 17h14h59
#    Se não houver nenhuma medida nesse horário, a coluna
#    das 17h00 é marcada como sem dados (NaN). Se houver mais de uma, é usada a última.
    

    result = []
    cols = {}
    hora_base = datetime(2010, 1, 1, 9, 0)
    intervalo = 15
    
    
    for i in range(0, 24 * 60 // intervalo):
        td = timedelta(minutes=i * intervalo)
        dia = 0 if (td + timedelta(hours=9)  ).days < 1 else 1
        horas = int(td.total_seconds() // 3600 + 9) % 24
        minutos = int(td.total_seconds() % 3600) //60
        
        # Não cria intervalos de "15 min" se o horario for no período noturno.
        # (a medida padrão do exame passa para uma leitura a cada 30min nesse horário)
        if minutos in (15, 45) and horario_noturno(horas):
            continue
        
        cols[td] = f"+{dia} {horas}:{minutos:02d}"

    if limit:
        limiter = range(limit)
    else:
        limiter = itertools.count()
   
    for _, (paciente_id, paciente) in zip(limiter, dados):
        
        data_inicial = paciente.dateitem.iloc[0].date()
        
        paciente_norm = pd.concat((paciente, normalize_date(paciente, "dateitem", name="normalized_ts") ), axis=1)
        
        whitecoat = extract_whitecoat(paciente_norm)
        
        # Imprime os dados brutos de um paciente a partir de um certo horário
        # pode ser usado para verificar se a funcionalidade de normalizar o horáio abaixo está pegando as medias corretas
        # print(paciente_norm[paciente_norm["normalized_ts"] > datetime(2010, 1, 2) ])
        
        
        linha_sist = []
        linha_diast = []
        
        erro_diurno = timedelta(minutes=15)
        erro_noturno = timedelta(minutes=30)
        
        for col in cols:
            hora_normalizada = hora_base + col
            erro = erro_noturno if horario_noturno(hora_normalizada.hour) else erro_diurno
            loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
            medida_sist = loc_medida.loc[:, "sistolica"]
            medida_diast = loc_medida.loc[:, "diastolica"]
               
            if not len(medida_sist):
                medida_sist = medida_diast = float("nan")
                
            else:
                medida_sist = medida_sist.values[-1]
                medida_diast = medida_diast.values[-1]
        
            linha_sist.append(medida_sist)
            linha_diast.append(medida_diast)
            # linha.append(paciente_norm[inicio_jan <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < final_jan].loc[:, coluna].mean())
            
        result.append(linha_sist + linha_diast + [whitecoat])
      
    colunas_sist = [f"sist {col.split()[-1]}" for col in cols.values()]
    colunas_diast = [f"diast {col.split()[-1]}" for col in cols.values()]
    coluna_whitecoat = ["whitecoat"]
    result = pd.DataFrame(result , columns=colunas_sist + colunas_diast + coluna_whitecoat)
    
    return result


In [14]:
lista_campos = ['numero_identificacao',
                 'nome',
                 'data_nascimento',
                 'genero',
                 'dateitem',
                 'sistolica',
                 'diastolica',
                 'data_exame']


mapas_dos_campos_hora_original = mapas_dos_campos[lista_campos]

hora_modificada = []
for item in mapas_dos_campos_hora_original['dateitem']:
    hora_modificada.append(item.strftime('%H:%M:%S'))
mapas_dos_campos_hora_original['dateitem'] = hora_modificada

#for item in range(len(mapas_dos_campos_hora_original['dateitem'])):
#    mapas_dos_campos_hora_original['dateitem'].iloc[item] = mapas_dos_campos_hora_original['dateitem'].iloc[item].strftime('%H:%M:%S')
    #mapas_dos_campos_hora_original['dateitem'][item] = mapas_dos_campos_hora_original['dateitem'][item].strftime('%H:%M:%S')
    

mapas_dos_campos_hora_original.to_csv(r"D:\PA_clean\dataset\pacientes_sem_carrossel.csv", 
                   sep=";", encoding="latin1", index=False)

mapas_dos_campos_hora_original

<ipython-input-14-d420ec5eb46f>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mapas_dos_campos_hora_original['dateitem'] = hora_modificada


numero_identificacao                                   nome  \
0                           4            DONIZZETTE PEREIRA DA SILVA   
1                           4            DONIZZETTE PEREIRA DA SILVA   
2                           4            DONIZZETTE PEREIRA DA SILVA   
3                           4            DONIZZETTE PEREIRA DA SILVA   
4                           4            DONIZZETTE PEREIRA DA SILVA   
...                       ...                                    ...   
1655823                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655824                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655825                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655826                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   
1655827                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   

        data_nascimento genero  dateitem  sistolica  diastolica  \
0            1923-10-05      M  12:39:00      140.0        80.0   
1            1923-10-05      M  12:48:00        NaN         NaN   
2            1923-10-05      M  13:03:00        NaN         NaN   
3            1923-10-05      M  13:18:00        NaN         NaN   
4            1923-10-05      M  13:33:00        NaN         NaN   
...                 ...    ...       ...        ...         ...   
1655823      1971-01-14      M  14:30:00      131.0        91.0   
1655824      1971-01-14      M  14:45:00      143.0        84.0   
1655825      1971-01-14      M  15:00:00      138.0        99.0   
1655826      1971-01-14      M  15:15:00      127.0        89.0   
1655827      1971-01-14      M  15:28:00        NaN         NaN   

                 data_exame  
0       2018-09-10 12:25:23  
1       2018-09-10 12:25:23  
2       2018-09-10 12:25:23  
3       2018-09-10 12:25:23  
4       2018-09-10 12:25:23  
...                     ...  
1655823 2020-09-10 17:42:01  
1655824 2020-09-10 17:42:01  
1655825 2020-09-10 17:42:01  
1655826 2020-09-10 17:42:01  
1655827 2020-09-10 17:42:01  

[1655828 rows x 8 columns]

In [15]:
%%capture --no-stderr
%time dados_transpostos = transpoe_medidas(mapas_por_paciente)

# dados_transpostos

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:22: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  primeiras_medidas = (paciente[paciente.dateitem >= primeira_medida][paciente.dateitem <= quarta_medida]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:22: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  primeiras_medidas = (paciente[paciente.dateitem >= primeira_medida][paciente.dateitem <= quarta_medida]
<ipython-input-13-051a40ca96ac>:94: UserWarning

...

<ipython-input-13-051a40ca96ac>:22: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  primeiras_medidas = (paciente[paciente.dateitem >= primeira_medida][paciente.dateitem <= quarta_medida]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:22: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  primeiras_medidas = (paciente[paciente.dateitem >= primeira_medida][paciente.dateitem <= quarta_medida]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-051a40ca96ac>:94: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  loc_medida = paciente_norm[hora_normalizada <= paciente_norm.normalized_ts][paciente_norm.normalized_ts < hora_normalizada + erro]
<ipython-input-13-05

In [16]:
dados_transpostos

sist 9:00  sist 9:15  sist 9:30  sist 9:45  sist 10:00  sist 10:15  \
0          105.0      108.0      116.0      104.0       106.0        98.0   
1          103.0      114.0       82.0      104.0        98.0       106.0   
2          147.0      148.0      156.0      140.0       130.0       132.0   
3          140.0      139.0      142.0      137.0       135.0       177.0   
4            NaN      110.0      101.0      108.0       111.0       111.0   
...          ...        ...        ...        ...         ...         ...   
21132      114.0      120.0      164.0      116.0       119.0       126.0   
21133      107.0      110.0      103.0        NaN         NaN         NaN   
21134        NaN        NaN        NaN        NaN         NaN         NaN   
21135       94.0      107.0      112.0      124.0       120.0        94.0   
21136      111.0      104.0      103.0      101.0        97.0       110.0   

       sist 10:30  sist 10:45  sist 11:00  sist 11:15  ...  diast 6:45  \
0             NaN       107.0         NaN         NaN  ...         NaN   
1           108.0       107.0       109.0       100.0  ...         NaN   
2           121.0       113.0       149.0       128.0  ...         NaN   
3           148.0       152.0       135.0       136.0  ...         NaN   
4           114.0       115.0       113.0       112.0  ...         NaN   
...           ...         ...         ...         ...  ...         ...   
21132       123.0         NaN       122.0       159.0  ...         NaN   
21133       114.0       144.0       128.0       104.0  ...         NaN   
21134         NaN         NaN         NaN         NaN  ...        68.0   
21135       102.0       113.0       104.0        96.0  ...         NaN   
21136       111.0       116.0       104.0       121.0  ...         NaN   

       diast 7:00  diast 7:15  diast 7:30  diast 7:45  diast 8:00  diast 8:15  \
0             NaN         NaN         NaN        67.0        61.0        69.0   
1            74.0         NaN         NaN         NaN        60.0        74.0   
2            93.0         NaN         NaN         NaN        86.0        87.0   
3            62.0         NaN       104.0         NaN         NaN        89.0   
4             NaN        93.0        68.0        91.0         NaN         NaN   
...           ...         ...         ...         ...         ...         ...   
21132        59.0        74.0        68.0        86.0         NaN       107.0   
21133        50.0        53.0        52.0        62.0        68.0        61.0   
21134        83.0        84.0        85.0         NaN         NaN         NaN   
21135        64.0        76.0         NaN        69.0        75.0        74.0   
21136         NaN        71.0        73.0        56.0        57.0        65.0   

       diast 8:30  diast 8:45  \
0            62.0        51.0   
1            70.0        67.0   
2            82.0        82.0   
3            90.0        72.0   
4            81.0        72.0   
...           ...         ...   
21132       106.0        93.0   
21133        64.0        60.0   
21134         NaN         NaN   
21135        69.0        67.0   
21136        68.0        82.0   

                                               whitecoat  
0      [('12:39', 140.0, 80.0), ('12:48', nan, nan), ...  
1      [('08:04', 114.0, 60.0), ('08:15', 111.0, 74.0...  
2      [('08:11', 133.0, 86.0), ('08:15', 137.0, 87.0...  
3      [('08:22', 153.0, 89.0), ('08:30', 153.0, 90.0...  
4      [('08:31', 106.0, 81.0), ('08:48', 116.0, 72.0...  
...                                                  ...  
21132  [('16:29', 115.0, 72.0), ('16:48', nan, nan), ...  
21133  [('16:51', 126.0, 68.0), ('17:00', 128.0, 60.0...  
21134  [('17:26', 106.0, 75.0), ('17:41', 112.0, 85.0...  
21135  [('17:54', 132.0, 77.0), ('18:03', nan, nan), ...  
21136  [('17:48', 107.0, 83.0), ('18:00', 114.0, 75.0...  

[21137 rows x 165 columns]

In [17]:
# Cria colunas de cabeçalho para cada exame, a partir do "mapa agrupado"
# 

def cria_cabecalho(mapas_agrupado):
    
    mapas = mapas_agrupado[["numero_identificacao", "data_nascimento", "genero", "idade", "peso", "altura", "data_exame"] ]
    #mapas_nome = mapas_nome_agrupado[["numero_identificacao", "nome", "data_nascimento", "genero", "idade", "peso", "altura", "data_exame"] ]
    #print(mapas)
    return mapas

mapas = cria_cabecalho(mapas_agrupado)



def cria_nome_cabecalho(mapas_nome_agrupado):
 
    mapas_nome = mapas_agrupado[["numero_identificacao", "nome", "data_nascimento", "genero", "idade", "peso", "altura", "data_exame"] ]
    print(mapas_nome)
    return mapas_nome

mapas_nome = cria_nome_cabecalho(mapas_agrupado)




       numero_identificacao                                   nome  \
0                         4            DONIZZETTE PEREIRA DA SILVA   
1                         5                JEFFERSON LUCENA DANTAS   
2                         6                    IGOR DAMASCENO MOTA   
3                         7              ANDREIA DE OLIVEIRA AVILA   
4                         8      CRISTIANO NASCIMENTO POMBO DA PAZ   
...                     ...                                    ...   
21132                 21787              CASTRUZ CATRAMBY COUTINHO   
21133                 21788                 TATIANE ROCHA DA SILVA   
21134                 21791                   MARCOS PAULO PEREIRA   
21135                 21792                      EULINA SOUZA DIAS   
21136                 21793  FERNANDO LUIZ DE AZEREDO COUTINHFILHO   

      data_nascimento genero  idade peso altura          data_exame  
0          1923-10-05      M   94.0   85    160 2018-09-10 12:25:23  
1          1948-10-

In [18]:
mapas_final = pd.concat([mapas.iloc[:, :], dados_transpostos],axis=1)
mapas_nome_final = pd.concat([mapas_nome.iloc[:, :], dados_transpostos],axis=1)
mapas_nome

#######################################################################################################################
mapas_final.to_csv(r"D:\PA_clean\dataset\pacientes_com_medidas_whitecoat.csv", 
                   sep=";", encoding="latin1", index=False)

mapas_nome_final.to_csv(r"D:\PA_clean\dataset\pacientes_com_medidas_comNOMES.csv", 
                   sep=";", encoding="latin1", index=False)

#mapas_final.to_csv(r"D:\Projeto_PA\dataset_modificado\pacientes_com_medidas_whitecoat_MAPA2021.csv", 
#                   sep=";", encoding="latin1", index=False)

In [19]:
mapas_final[mapas_final['numero_identificacao'] == 13659]

numero_identificacao data_nascimento genero  idade peso altura  \
13287                 13659      1978-08-30      F   41.0   86   1,72   

               data_exame  sist 9:00  sist 9:15  sist 9:30  ...  diast 6:45  \
13287 2019-12-02 09:09:58        NaN      113.0        NaN  ...         NaN   

       diast 7:00  diast 7:15  diast 7:30  diast 7:45  diast 8:00  diast 8:15  \
13287        76.0        81.0        79.0        80.0        66.0        78.0   

       diast 8:30  diast 8:45  whitecoat  
13287         NaN         NaN         []  

[1 rows x 172 columns]

## Dataset com desfechos coletados a partir dos pacientes da base de dados

In [20]:
#with open(filepath,'r',encoding='utf-8-sig') as f:
#    texto = f.read()
#    texto = texto.replace(',',';')
#    with open(filepath2,'w',encoding='latin1') as f2:
#        f2.write(texto)

In [21]:
def to_date(date):
    if isinstance(date,str):
        return datetime.strptime(data, "%d/%m/%Y").strftime('%Y-%m-%d')
    return None

In [22]:
filepath = DIR_DESFECHO / "dataset" / "original" / r'CaReABPM_DATA_2022-12-06_1933.csv'
filepath2 = DIR_DESFECHO / "dataset" / "original" / r'CaReABPM_DATA_2022-12-06_1933_2.csv'

dados_brutos = pd.read_csv(filepath2,encoding='latin1',sep=';')

In [23]:
#dados_brutos['day_of_birth'] = dados_brutos['day_of_birth'].apply(to_date)
#dados_brutos.to_csv(filepath2,sep=";", encoding="latin1", index=False)

In [24]:
#dados_brutos = dados_brutos.drop(['∩╗┐study_id',
dados_brutos = dados_brutos.drop(
['study_id',
'redcap_data_access_group',
'filling_date_f11_v1',
'filling_date_f12_v1',
'medical_record_num',
'scholarity_level',
'scholarity_years',
'family_income',
'civil_status',
'telefone_1',
'telefone_2',
'telefone_3'], axis=1)
dados_brutos.head()


name day_of_birth   age  gender  \
0                            CLAUDIO SASAOKA   1968-03-12  53.0     1.0   
1              PEDRO AUGUSTO LEMOS DE CASTRO   1980-05-01  41.0     1.0   
2            DANYELLE COELHO DE ARAUJO SOUSA   2000-05-01  21.0     0.0   
3        MARIA DE FATIMA ALMEIDA DE CARMARGO   1954-03-01  67.0     0.0   
4  Ana Elisabeth da Silveira Calado Siqueira   1958-09-24  63.0     0.0   

  comments_f14_v  demografia_complete  hbp    date_htn   dm date_dm  ...  \
0            NaN                    2  0.0         NaN  0.0     NaN  ...   
1            NaN                    2  1.0         NaN  0.0     NaN  ...   
2            NaN                    2  0.0         NaN  0.0     NaN  ...   
3            NaN                    0  NaN         NaN  NaN     NaN  ...   
4            NaN                    2  1.0  2017-02-24  0.0     NaN  ...   

   mech_complication_mi___4 outcome_thrombus  outcome_nosocom_infect_v  \
0                         0              NaN                       NaN   
1                         0              NaN                       NaN   
2                         0              0.0                       0.0   
3                         0              NaN                       NaN   
4                         0              NaN                       NaN   

   outcome_hyperglycemia_v  gastrointest_bleed_v  outcome_hb_drop_v  \
0                      NaN                   NaN                NaN   
1                      NaN                   NaN                NaN   
2                      0.0                   0.0                0.0   
3                      NaN                   NaN                NaN   
4                      NaN                   NaN                NaN   

   outcome_neutropenia_v  outcome_transaminase_v  comments_f16_v  \
0                    NaN                     NaN             NaN   
1                    NaN                     NaN             NaN   
2                    0.0                     0.0             NaN   
3                    NaN                     NaN             NaN   
4                    NaN                     NaN             NaN   

   desfechos_complete  
0                   0  
1                   2  
2                   2  
3                   0  
4                   0  

[5 rows x 206 columns]

In [25]:
dados_brutos.sort_values(by='name')

name day_of_birth   age  gender  \
455                    01/07/1954   1962-09-16  59.0     1.0   
534                    05/09/1982          NaN   NaN     0.0   
669                    11/01/1972          NaN   NaN     0.0   
631                    13/03/1969   1969-03-13  52.0     0.0   
413                        241076   1942-03-05  79.0     1.0   
...                           ...          ...   ...     ...   
189        ZULEICA GUEDE PELLICER   1960-07-31  61.0     0.0   
234                   jair severo   1948-05-28  73.0     1.0   
238   laura porto de deus vieira    1980-08-12  41.0     0.0   
250         odete antonia ribeiro   1958-01-02  63.0     0.0   
1142                          NaN          NaN   NaN     NaN   

               comments_f14_v  demografia_complete  hbp    date_htn   dm  \
455                       NaN                    2  1.0         NaN  1.0   
534                       NaN                    2  1.0  2019-07-19  0.0   
669                       NaN                    2  NaN         NaN  NaN   
631                       NaN                    2  NaN         NaN  NaN   
413                       NaN                    2  1.0         NaN  0.0   
...                       ...                  ...  ...         ...  ...   
189                       NaN                    2  1.0         NaN  0.0   
234   sem telefone registrado                    2  1.0  2018-11-20  0.0   
238                       NaN                    2  0.0         NaN  0.0   
250                       NaN                    2  1.0  2019-01-22  NaN   
1142                      NaN                    0  NaN         NaN  NaN   

     date_dm  ...  mech_complication_mi___4 outcome_thrombus  \
455      NaN  ...                         0              0.0   
534      NaN  ...                         0              0.0   
669      NaN  ...                         0              0.0   
631      NaN  ...                         0              NaN   
413      NaN  ...                         0              0.0   
...      ...  ...                       ...              ...   
189      NaN  ...                         0              0.0   
234      NaN  ...                         0              NaN   
238      NaN  ...                         0              NaN   
250      NaN  ...                         0              NaN   
1142     NaN  ...                         0              NaN   

      outcome_nosocom_infect_v  outcome_hyperglycemia_v  gastrointest_bleed_v  \
455                        0.0                      0.0                   0.0   
534                        0.0                      0.0                   0.0   
669                        0.0                      0.0                   0.0   
631                        NaN                      NaN                   NaN   
413                        0.0                      0.0                   0.0   
...                        ...                      ...                   ...   
189                        0.0                      0.0                   0.0   
234                        NaN                      NaN                   NaN   
238                        NaN                      NaN                   NaN   
250                        NaN                      NaN                   NaN   
1142                       NaN                      NaN                   NaN   

      outcome_hb_drop_v  outcome_neutropenia_v  outcome_transaminase_v  \
455                 0.0                    0.0                     0.0   
534                 0.0                    0.0                     0.0   
669                 0.0                    0.0                     0.0   
631                 NaN                    NaN                     NaN   
413                 0.0                    0.0                     0.0   
...                 ...                    ...                     ...   
189                 0.0                    0.0                     0.0   
234          

In [26]:
for campo in dados_brutos.sort_values(by='name')['name']:
    print(campo)


01/07/1954
05/09/1982
11/01/1972
13/03/1969
241076
248580
261421
27/02/1987
285780
286186
29/09/1957
432345
446886
461456
ABERCINA MARIA DA COSTA
ADALBERTO FREIRE BARBOSA FILHO
ADALGIZA DE OLIVEIRA LISBOA
ADAO JEOVA FILHO
ADEIDES RODRIGUES BORGES JUNIOR
ADELAIDE CHAVES AZEVEDO E SILVA
ADELIA SANTA CRUZ DA SILVA
ADEMAR GUSMAO PEREZ
ADEMIR BRAZ DA SILVA
ADEMIR DAMASCENO SIMOES
ADILENE ALVES DA ASSUNCAO
ADMAR PAMPLONA ARAUJO
ADMILSON QUEIROZ DE SOUZA
ADRIANA LACERDA LIMA
ADRIANA ROSA PESCINELLI
ADRIANO SILVA ARANTES
ADROALDO DE SOUZA VARGAS
AEDJA MARIA VALENCA MONTEIRO
AIDA PEREIRA DE ARAUJO
AIRLIS LUIS FERRACIOLI
AIRTON BASTOS DE JESUS
ALAIDES PEREIRA DA SILVA
ALBERONE HELENO REZENDE CAMPOS
ALBERTO RODRIGO DA COSTA CARNEIRO DE ARAUJO
ALCILENE AZEVEDO
ALCY LOPES DA CRUZ
ALDAHIR LEITE
ALDEIDE DUARTE MARTINS
ALENYR ANTUNES
ALESSANDRO AUGUSTO SGANZERLA
ALEX ALMEIDA E SILVA
ALEX DE OLIVEIRA
ALEX PAULO DE SOUZA
ALEXANDER XAVIER DA SILVA
ALEXANDRE ALVES DOS SANTOS
ALEXANDRE VIEIRA DE OLIVEIRA
A

In [27]:
#teste = mapas_nome_final[['data_nascimento','genero']].sort_values(by='data_nascimento')

In [28]:
#len(set(teste['data_nascimento']))

In [29]:
dados_brutos

name day_of_birth   age  gender  \
0                               CLAUDIO SASAOKA   1968-03-12  53.0     1.0   
1                 PEDRO AUGUSTO LEMOS DE CASTRO   1980-05-01  41.0     1.0   
2               DANYELLE COELHO DE ARAUJO SOUSA   2000-05-01  21.0     0.0   
3           MARIA DE FATIMA ALMEIDA DE CARMARGO   1954-03-01  67.0     0.0   
4     Ana Elisabeth da Silveira Calado Siqueira   1958-09-24  63.0     0.0   
...                                         ...          ...   ...     ...   
1214                         MARLENE DIAS FEIJO   1964-02-15  58.0     0.0   
1215                      SIDNEI CORREA MARQUES   1953-06-25  69.0     1.0   
1216                             VANDI DA COSTA   1943-03-23  79.0     0.0   
1217                    UBIRACY TEIXEIRA BRAZAO   1938-08-11  84.0     1.0   
1218     MARIA APARECIDA PINTO DIAS DE CARVALHO   1956-10-03  66.0     0.0   

     comments_f14_v  demografia_complete  hbp    date_htn   dm date_dm  ...  \
0               NaN                    2  0.0         NaN  0.0     NaN  ...   
1               NaN                    2  1.0         NaN  0.0     NaN  ...   
2               NaN                    2  0.0         NaN  0.0     NaN  ...   
3               NaN                    0  NaN         NaN  NaN     NaN  ...   
4               NaN                    2  1.0  2017-02-24  0.0     NaN  ...   
...             ...                  ...  ...         ...  ...     ...  ...   
1214            NaN                    2  NaN         NaN  1.0     NaN  ...   
1215            NaN                    2  1.0         NaN  0.0     NaN  ...   
1216            NaN                    2  NaN         NaN  NaN     NaN  ...   
1217            NaN                    2  0.0         NaN  0.0     NaN  ...   
1218            NaN                    2  NaN         NaN  NaN     NaN  ...   

      mech_complication_mi___4 outcome_thrombus  outcome_nosocom_infect_v  \
0                            0              NaN                       NaN   
1                            0              NaN                       NaN   
2                            0              0.0                       0.0   
3                            0              NaN                       NaN   
4                            0              NaN                       NaN   
...                        ...              ...                       ...   
1214                         0              0.0                       0.0   
1215                         0              0.0                       0.0   
1216                         0              NaN                       NaN   
1217                         0              0.0                       0.0   
1218                         0              NaN                       NaN   

      outcome_hyperglycemia_v  gastrointest_bleed_v  outcome_hb_drop_v  \
0                         NaN                   NaN                NaN   
1                         NaN                   NaN                NaN   
2                         0.0                   0.0                0.0   
3                         NaN                   NaN                NaN   
4                         NaN                   NaN                NaN   
...                       ...                   ...                ...   
1214                      0.0                   0.0                0.0   
1215                      0.0                   0.0                0.0   
1216                      NaN                   NaN                NaN   
1217                      0.0                   0.0                0.0   
1218                      NaN                   NaN                NaN   

      outcome_neutropenia_v  outcome_transaminase_v  comments_f16_v  \
0                       NaN                     NaN             NaN   
1                       NaN                     NaN             NaN   
2                       0.0                     0.0             NaN   
3                       NaN                     NaN        

In [30]:
dados_brutos.iloc[0,0]

'CLAUDIO SASAOKA'

In [31]:
#mapas_nome_final.query('data_nascimento == "1962-11-20"')
#mapas_nome_final.query('nome == "MARIA TEREZA GUEDES REZENDE"')

In [32]:
mapas_nome_final.loc[:,['data_nascimento','idade','genero']].head()

data_nascimento  idade genero
0      1923-10-05   94.0      M
1      1948-10-07   70.0      M
2      1999-03-23   19.0      M
3      1978-01-26   40.0      F
4      1990-03-07   28.0      M

In [33]:
nf = 0
lista_nf = []
lista_encontrados = []
lista_buscar = dados_brutos.index
#lista_buscar = dados_brutos.index[:10]
for linha in lista_buscar:
    controle = 0
    nome = str(dados_brutos.loc[linha,'name']).split(' ')[0].upper()
    nome1 = dados_brutos.loc[linha,'name']
    #print(f'\n\n\======={linha +1} - {nome} =======')
    #print(f"Nome:{nome}")
    #print(f"Nome1:{nome1}")
    data1 = dados_brutos.loc[linha,'day_of_birth']
    #data1 = data1.iloc[0]
    #print(repr(data1))
    genero1 = dados_brutos.loc[linha,'gender']
    #print(f'Data1:{data1}')
    #print(f'Genero1:{genero1}')
    if genero1 == 1.0:
        genero1 = 'M'
        #print('genero M')
    else:
        genero1 = 'F'
        #print('genero F')
    for linha2 in mapas_nome_final.index:
        nome2 = mapas_nome_final.loc[linha2,'nome'].upper()
        data2 = mapas_nome_final.loc[linha2,'data_nascimento']
        #print(f'Data2.1: {data2}')
        data2 = data2.to_pydatetime()
        #print(f'Data2.2: {data2}')
        #print(f'Data1:{data1}')
        try:
            data2 = datetime.strftime(data2, '%Y-%m-%d')
            #print(f'data2:{data2}')
        except:
            #print('Erro na data')
            pass
        #print('data2_',repr(data2))
        genero2 =mapas_nome_final.loc[linha2,'genero']
        # Batimento do conteúdo do banco de dados com o csv considerando as chaves: nome, data nasc e gênero
        #print(repr(nome),repr(nome2))
        if nome in nome2:
            #print('Nome contido')
            #print(repr(data1),repr(data2))
            #print(repr(genero1),repr(genero2))
            if data1 == data2 and genero1 == genero2:
               # print("Data e genero iguais")
                #print(mapas_nome_final.iloc[linha2,:])
                #print(repr(dados_brutos.iloc[linha,:]))
                #print(repr(mapas_nome_final.iloc[linha2,:]))
                lista_encontrados.append(pd.concat([mapas_nome_final.loc[linha2,:],dados_brutos.loc[linha,:]],axis=0))
                #lista_encontrados[-1] = lista_encontrados[-1].append(dados_brutos.iloc[linha,:])
                #print(lista_encontrados[-1])
                controle += 1
    #print("Fim busca pessoa")
    if controle == 0:
        nf += 1
        #print('Não encontrado')
        #print(f'\n\n\n{10*"="} {linha +1} {10*"="}\nNOME: {nome1}\nData: {data1}\nGenero: {genero1}\n')
        #print(f"Não Encontrado - QTD: {nf}")
        lista_nf.append(dados_brutos.loc[linha,:])

#print(f'Não Encontrados = {nf}')
print(f'Total:{len(lista_buscar)}')
print(f'Encontrados:{len(lista_encontrados)}')
print(f'Não encontrados:{len(lista_nf)}')
print(f'Econtrados a mais:{len(lista_encontrados) - (len(lista_buscar) - len(lista_nf))}')

Total:1219
Encontrados:1408
Não encontrados:79
Econtrados a mais:268


In [34]:
#for i in lista_encontrados:
#   print(f'nome:{i.nome}\tdata:{i.data_nascimento}\tgenero:{i.genero}')

In [35]:
df_encontrados = pd.DataFrame(lista_encontrados)
df_encontrados = df_encontrados.drop([
'name',
'day_of_birth',
'age',
'gender'
],axis=1)
df_encontrados.to_csv(DIR_DESFECHO / "dataset" / 'comdesfecho_Encontrados.csv',sep=';', 
                      encoding='Latin1',index=False) 
# encoding='utf-8', dtype={'sist 9:00':int})
df_encontrados.head()

numero_identificacao                                  nome data_nascimento  \
0                  3766                       CLAUDIO SASAOKA      1968-03-12   
1                  9201         PEDRO AUGUSTO LEMOS DE CASTRO      1980-05-01   
2                 12770       DANYELLE COELHO DE ARAUJO SOUSA      2000-05-01   
3                  6295       MARGARIDA MARIA DE BRITO RABELO      1954-03-01   
4                   883  ANA ELIZABETH DA SILVEIRA C.SIQUEIRA      1958-09-24   

  genero  idade peso altura          data_exame  sist 9:00  sist 9:15  ...  \
0      M   51.0   95   1,84 2019-03-27 14:41:24      119.0      119.0  ...   
1      M   39.0   76    162 2019-08-06 09:08:09        NaN        NaN  ...   
2      F   19.0   85    158 2019-11-06 13:34:16       98.0      116.0  ...   
3      F   65.0   63    163 2019-05-28 10:27:03      134.0      124.0  ...   
4      F   60.0   68   1,53 2019-01-28 11:04:12      129.0      127.0  ...   

   mech_complication_mi___4  outcome_thrombus  outcome_nosocom_infect_v  \
0                         0               NaN                       NaN   
1                         0               NaN                       NaN   
2                         0               0.0                       0.0   
3                         0               NaN                       NaN   
4                         0               NaN                       NaN   

   outcome_hyperglycemia_v  gastrointest_bleed_v  outcome_hb_drop_v  \
0                      NaN                   NaN                NaN   
1                      NaN                   NaN                NaN   
2                      0.0                   0.0                0.0   
3                      NaN                   NaN                NaN   
4                      NaN                   NaN                NaN   

   outcome_neutropenia_v  outcome_transaminase_v  comments_f16_v  \
0                    NaN                     NaN             NaN   
1                    NaN                     NaN             NaN   
2                    0.0                     0.0             NaN   
3                    NaN                     NaN             NaN   
4                    NaN                     NaN             NaN   

   desfechos_complete  
0                   0  
1                   2  
2                   2  
3                   0  
4                   0  

[5 rows x 375 columns]

In [36]:
len(lista_nf), len(lista_encontrados)

(79, 1408)

#df_encontrados['cabg']

In [37]:
for i in df_encontrados.loc[:,'comments_f14_v':].columns:
    print(i)

comments_f14_v
demografia_complete
hbp
date_htn
dm
date_dm
smoking
smoking_cessation_date
smoking_burden
comorb_hf
time_diagnosis_hf
nyha_preadm
hf_chagas
hf_ischemia
hf_valvular
hf_cardiomyopathy
hf_hypertension
hf_other
chronic_liver_failure
chronic_liver_failure_et
date_liver_failure
cad
acs_last_episode
acs_last_episode_type
acs_last_episode_date
cabg
cabg_date
pci
pci_date
periph_art_obstr_dis
electronicdev_adm
cerebrovasc_dis
cerebrovasc_dis_date
cerebrovasc_dis_type___0
cerebrovasc_dis_type___1
cerebrovasc_dis_type___2
cerebrovasc_dis_type___3
asthma
copd
copd_date
sleep_apnea
obesity
hypothyroidism
hyperthyroidism
ckd
ckd_dialisis
ckd_stage
cancer
malignancy_type___0
malignancy_type___1
malignancy_type___2
malignancy_type___3
malignancy_type___4
malignancy_type___5
malignancy_type___6
malignancy_type___7
malignancy_type_other
anemia
major_depression
immunosupression
immunosupression_cause
comments_f10_v1
comorbidades_complete
filling_date_f3_v1
home_meds_spironolactone
home_med

In [38]:
#len(lista_nf)

In [39]:
nao_encontrados = pd.DataFrame(lista_nf)
nao_encontrados.to_csv(DIR_DESFECHO / "dataset" / 'comdesfecho_naoencontrados.csv',
                       sep=';', encoding='latin1', index=False)
nao_encontrados

name day_of_birth   age  gender  comments_f14_v  \
10        MARIA DE FATIMA DA SILVA   1953-10-13  67.0     0.0             NaN   
13    Maria Aparecida Marins Lopes   1951-11-04  69.0     0.0             NaN   
23          LEANDRO ALVES DE JESUS   1980-03-01  41.0     1.0             NaN   
24                JAIRO VAZ BONFIM   1944-04-02  77.0     1.0             NaN   
45    VANDA MARIA DE MATTOS VIEIRA   1951-08-19  70.0     0.0             NaN   
...                            ...          ...   ...     ...             ...   
1142                           NaN          NaN   NaN     NaN             NaN   
1143       LEONARDO OLIVEIRA SINGH   2000-07-09  22.0     1.0             NaN   
1152    ERBESON FERNANDES DA SILVA   1984-10-24  37.0     NaN             NaN   
1167    CECILIA DA SILVA GONCALVES   2007-05-01  15.0     0.0             NaN   
1197       JAILSON MANGUEIRA ASSIS   1974-07-19  48.0     1.0             NaN   

      demografia_complete  hbp date_htn   dm  date_dm  ...  \
10                      2  NaN      NaN  NaN      NaN  ...   
13                      2  0.0      NaN  0.0      NaN  ...   
23                      2  NaN      NaN  NaN      NaN  ...   
24                      2  1.0      NaN  0.0      NaN  ...   
45                      2  NaN      NaN  NaN      NaN  ...   
...                   ...  ...      ...  ...      ...  ...   
1142                    0  NaN      NaN  NaN      NaN  ...   
1143                    2  0.0      NaN  0.0      NaN  ...   
1152                    2  1.0      NaN  0.0      NaN  ...   
1167                    2  NaN      NaN  NaN      NaN  ...   
1197                    2  1.0      NaN  0.0      NaN  ...   

      mech_complication_mi___4 outcome_thrombus  outcome_nosocom_infect_v  \
10                           0              NaN                       NaN   
13                           0              NaN                       0.0   
23                           0              NaN                       NaN   
24                           0              NaN                       NaN   
45                           0              NaN                       NaN   
...                        ...              ...                       ...   
1142                         0              NaN                       NaN   
1143                         0              0.0                       0.0   
1152                         0              NaN                       NaN   
1167                         0              NaN                       NaN   
1197                         0              0.0                       0.0   

      outcome_hyperglycemia_v  gastrointest_bleed_v  outcome_hb_drop_v  \
10                        NaN                   NaN                NaN   
13                        0.0                   0.0                0.0   
23                        NaN                   NaN                NaN   
24                        NaN                   NaN                NaN   
45                        NaN                   NaN                NaN   
...                       ...                   ...                ...   
1142                      NaN                   NaN                NaN   
1143                      0.0                   0.0                0.0   
1152                      NaN                   NaN                NaN   
1167                      NaN                   NaN                NaN   
1197                      0.0                   0.0                0.0   

      outcome_neutropenia_v  outcome_transaminase_v  comments_f16_v  \
10                      NaN                     NaN             NaN   
13                      0.0                     0.0             NaN   
23                      NaN                     NaN             NaN   
24                      NaN                     NaN             NaN   
45                      NaN                     NaN             NaN   
...                     ...                     ...             ...   
1

In [40]:
dados_brutos[dados_brutos['name'] == 'DONIZZETTE PEREIRA DA SILVA']

name day_of_birth   age  gender comments_f14_v  \
935  DONIZZETTE PEREIRA DA SILVA   1923-10-05  98.0     0.0            NaN   

     demografia_complete  hbp date_htn   dm date_dm  ...  \
935                    2  1.0      NaN  1.0     NaN  ...   

     mech_complication_mi___4 outcome_thrombus  outcome_nosocom_infect_v  \
935                         0              0.0                       0.0   

     outcome_hyperglycemia_v  gastrointest_bleed_v  outcome_hb_drop_v  \
935                      0.0                   0.0                0.0   

     outcome_neutropenia_v  outcome_transaminase_v  comments_f16_v  \
935                    0.0                     0.0             NaN   

     desfechos_complete  
935                   2  

[1 rows x 206 columns]